In [ ]:
!nvidia-smi

Fri Sep 10 12:22:20 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.63.01    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla K80           Off  | 00000000:00:04.0 Off |                    0 |
| N/A   56C    P8    32W / 149W |      0MiB / 11441MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
!git clone https://github.com/mrazizi/Generating_Text_Summary_With_GPT2.git

Cloning into 'Generating_Text_Summary_With_GPT2'...
remote: Enumerating objects: 4177, done.
remote: Counting objects: 100% (4177/4177), done.
remote: Compressing objects: 100% (4123/4123), done.
remote: Total 4177 (delta 75), reused 4143 (delta 49), pack-reused 0
Receiving objects: 100% (4177/4177), 12.64 MiB | 20.10 MiB/s, done.
Resolving deltas: 100% (75/75), done.


In [ ]:
%cd /content/Generating_Text_Summary_With_GPT2

/content/Generating_Text_Summary_With_GPT2


In [ ]:
!pip3 install -r requirements.txt

     |████████████████████████████████| 776.8 MB 18 kB/s 
     |████████████████████████████████| 45 kB 3.4 MB/s 
     |████████████████████████████████| 364 kB 47.3 MB/s 
     |████████████████████████████████| 131 kB 48.7 MB/s 
     |████████████████████████████████| 895 kB 53.2 MB/s 
     |████████████████████████████████| 1.2 MB 34.7 MB/s 
     |████████████████████████████████| 61 kB 5.8 MB/s 
     |████████████████████████████████| 115 kB 51.9 MB/s 
     |████████████████████████████████| 7.9 MB 34.0 MB/s 
     |████████████████████████████████| 79 kB 7.1 MB/s 
     |████████████████████████████████| 138 kB 56.4 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0
  Attempting uninstall: tqdm
    Found existin

In [ ]:
!pip install wandb
import wandb
wandb.init()

     |████████████████████████████████| 1.7 MB 13.2 MB/s 
     |████████████████████████████████| 179 kB 53.7 MB/s 
     |████████████████████████████████| 97 kB 6.6 MB/s 
     |████████████████████████████████| 133 kB 52.8 MB/s 
     |████████████████████████████████| 63 kB 1.7 MB/s 
  Created wheel for subprocess32: filename=subprocess32-3.5.4-py3-none-any.whl size=6502 sha256=84ea2fc69d530b88fc6d315c073b3369bd072e2657e66771b507db0f021550d5
  Stored in directory: /root/.cache/pip/wheels/50/ca/fa/8fca8d246e64f19488d07567547ddec8eb084e8c0d7a59226a
  Created wheel for pathtools: filename=pathtools-0.1.2-py3-none-any.whl size=8807 sha256=374e45901fa22cbf003f617446f49b4b2dc3fd2cc6539a2e36a60fa54a76de03
  Stored in directory: /root/.cache/pip/wheels/3e/31/09/fa59cef12cdcfecc627b3d24273699f390e71828921b2cbba2
Successfully built subprocess32 pathtools


<IPython.core.display.Javascript object>

wandb: You can find your API key in your browser here: https://wandb.ai/authorize


wandb: Paste an API key from your profile and hit enter: ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [ ]:
import argparse
from datetime import datetime
import os
import time

import numpy as np
from transformers import GPT2LMHeadModel,AdamW
from transformers.optimization import get_linear_schedule_with_warmup
from torch.utils.tensorboard import SummaryWriter
import torch
from torch.nn import CrossEntropyLoss
import torch.nn.functional as F
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler
from tqdm import tnrange, tqdm_notebook

from dataset import GPT21024Dataset 
from utils import add_special_tokens, generate_sample, set_seed

In [ ]:
#please change default arguments if needed

parser = argparse.ArgumentParser()
parser.add_argument("--lr",default=5e-5, type=float, help="learning rate")
parser.add_argument("--seed",default=42, type=int,  help="seed to replicate results")
parser.add_argument("--n_gpu",default=1, type=int,  help="no of gpu available")
parser.add_argument("--gradient_accumulation_steps",default=2, type=int, help="gradient_accumulation_steps")
parser.add_argument("--batch_size",default=1, type=int,  help="batch_size")
parser.add_argument("--num_workers",default=4, type=int,  help="num of cpus available")
parser.add_argument("--device",default=torch.device('cuda'), help="torch.device object")
parser.add_argument("--num_train_epochs",default=1, type=int,  help="no of epochs of training")
parser.add_argument("--output_dir",default='./output', type=str,  help="path to save evaluation results")
parser.add_argument("--model_dir",default='./weights', type=str,  help="path to save trained model")
parser.add_argument("--max_grad_norm",default=1.0, type=float, help="max gradient norm.")
parser.add_argument("--root_dir",default='./CNN/gpt2_1024_data', type=str, help="location of json dataset.")
parser.add_argument("--ids_file",default='./CNN/ids.json', type=str, help="location of train, valid and test file indexes")
args = parser.parse_args([])
print(args)

Namespace(batch_size=1, device=device(type='cuda'), gradient_accumulation_steps=2, ids_file='./CNN/ids.json', lr=5e-05, max_grad_norm=1.0, model_dir='./weights', n_gpu=1, num_train_epochs=1, num_workers=4, output_dir='./output', root_dir='./CNN/gpt2_1024_data', seed=42)


In [ ]:
def train(args, model, tokenizer, train_dataset, valid_dataset, ignore_index):
    """ Trains GPT2 model and logs necessary details.
        Args:
            args: dict that contains all the necessary information passed by user while training
            model: finetuned gpt/gpt2 model
            tokenizer: GPT/GPT2 tokenizer
            train_dataset: GPT21024Dataset object for training data
            ignore_index: token not considered in loss calculation
    """
    writer = SummaryWriter('./output/logs')
    train_sampler = RandomSampler(train_dataset)
    train_dl = DataLoader(train_dataset,sampler=train_sampler,batch_size=args.batch_size,num_workers=args.num_workers)
    loss_fct = CrossEntropyLoss(ignore_index=ignore_index) #ignores padding token for loss calculation
    optimizer = AdamW(model.parameters(),lr=args.lr)
    scheduler = get_linear_schedule_with_warmup(optimizer, 100, 80000)
    # scheduler = WarmupLinearSchedule(optimizer,100,80000)

    global_step = 0
    tr_loss, logging_loss = 0.0, 0.0
    model.zero_grad()
    train_iterator = tnrange(int(args.num_train_epochs), desc="Epoch")
    set_seed(args)
    for i, _ in enumerate(train_iterator):
        print(f"[LOG] epoch {i}/{args.num_train_epochs}")
        epoch_iterator = tqdm_notebook(train_dl, desc="Training")
        for step, batch in enumerate(epoch_iterator):
            print(f"[LOG] step {step}/{len(epoch_iterator)}")
            batch_a = time.time()
            
            inputs, labels = batch['article'].to(args.device), batch['article'].to(args.device)
            model.train()
            logits = model(inputs)[0]
            # only consider loss on reference summary just like seq2seq models
            shift_logits = logits[..., batch['sum_idx']:-1, :].contiguous()
            shift_labels = labels[..., batch['sum_idx']+1:].contiguous()
            loss = loss_fct(shift_logits.view(-1, shift_logits.size(-1)), shift_labels.view(-1))
            loss = loss/args.gradient_accumulation_steps
            loss.backward()
            torch.nn.utils.clip_grad_norm_(model.parameters(), args.max_grad_norm)
            tr_loss += loss.item()
            if (step + 1) % args.gradient_accumulation_steps == 0:
                optimizer.step()
                scheduler.step()  # Update learning rate schedule
                model.zero_grad()
                global_step += 1
                writer.add_scalar('lr', scheduler.get_lr()[0], global_step)
                writer.add_scalar('loss', (tr_loss - logging_loss)/args.gradient_accumulation_steps, global_step)
                logging_loss = tr_loss
                print("loss:", loss.item(), end='\n\n')
                if (step + 1)/args.gradient_accumulation_steps == 1.0:
                	print('After 1st update: ', end='\n\n')
                	generate_sample(valid_dataset, tokenizer, model, num=2, eval_step=False,device=args.device)
                
                
            if (step + 1) % (10*args.gradient_accumulation_steps) == 0:
                results = evaluate(args, model, valid_dataset, ignore_index, global_step)
                for key, value in results.items():
                    writer.add_scalar('eval_{}'.format(key), value, global_step)
                print('After', global_step+1,'updates: ', end='\n\n')
                generate_sample(valid_dataset, tokenizer, model, num=2, eval_step=True,device=args.device)

                print(f"Saving trained model...")
                model_directory_path = "/content/drive/MyDrive/MSC/My_Msc/Thesis/codes/gpt2_models"
                model_file = f"{model_directory_path}/{i}_{step}_model.bin"
                config_file = f"{model_directory_path}/{i}_{step}_config.json"
                torch.save(model.state_dict(), model_file)
                model.config.to_json_file(config_file)


            batch_b = time.time()
            print(f"[LOG] batch {batch} took {batch_b - batch_a}")

In [ ]:
def evaluate(args, model, eval_dataset, ignore_index, global_step=None):
    """ Returns perplexity score on validation dataset.
        Args:
            args: dict that contains all the necessary information passed by user while training
            model: finetuned gpt/gpt2 model
            eval_dataset: GPT21024Dataset object for validation data
            global_step: no. of times gradients have backpropagated
            ignore_index: token not considered in loss calculation
    """
    if not os.path.exists(args.output_dir):
        os.mkdir(args.output_dir)
    eval_output_dir = args.output_dir

    results = {}
    eval_sampler = SequentialSampler(eval_dataset)
    eval_dataloader = DataLoader(eval_dataset, sampler=eval_sampler, batch_size=args.batch_size)
    loss_fct = CrossEntropyLoss(ignore_index=ignore_index) #ignores padding token for loss calculation

    eval_loss = 0.0
    nb_eval_steps = 0
    model.eval()

    for batch in tqdm_notebook(eval_dataloader, desc="Evaluating"):
        inputs, labels = batch['article'].to(args.device), batch['article'].to(args.device)
        
        with torch.no_grad():
            logits = model(inputs)[0]
            idx = batch['sum_idx'].item() # index of separator token
            # only consider loss on reference summary just like seq2seq models
            shift_logits = logits[..., batch['sum_idx']:-1, :].contiguous()
            shift_labels = labels[..., batch['sum_idx']+1:].contiguous()
            lm_loss = loss_fct(shift_logits.view(-1, shift_logits.size(-1)), shift_labels.view(-1))
            eval_loss += lm_loss.mean().item()
        nb_eval_steps += 1

    eval_loss = eval_loss / nb_eval_steps
    perplexity = torch.exp(torch.tensor(eval_loss))

    result = {
        "perplexity": perplexity
    }
    print("perplexity:", perplexity.item())

    if global_step:
        output_eval_file = os.path.join(eval_output_dir, "eval_results.txt")
        with open(output_eval_file, "a") as f:
            for key in sorted(result.keys()):
                f.write('\n\n')
                f.write("time = %s, %s = %s, step = %s\n" % (datetime.now().strftime("%d/%m/%Y %H:%M:%S"), key, str(result[key]), str(global_step)))
    return result 

In [ ]:
# creating training and validation dataset object

train_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='train',length=3000) #training on only 3000 datasets
valid_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='valid',length=500)  #validation on only 500 datasets

In [ ]:
# load pretrained GPT2
tokenizer = add_special_tokens()
ignore_idx = tokenizer.pad_token_id
model = GPT2LMHeadModel.from_pretrained('gpt2')
model.resize_token_embeddings(len(tokenizer))
model.to(args.device)

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50259, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): Laye

In [ ]:
#training the model

start = time.time()
train(args, model, tokenizer, train_data, valid_data, ignore_idx)
print('total time: ', (time.time()-start)/60, " minutes", end='\n\n')

print('Saving trained model...')
model_directory_path = "/content/drive/MyDrive/MSC/My_Msc/Thesis/codes/gpt2_models"
model_file = f"{model_directory_path}/final_model.bin"
config_file = f"{model_directory_path}/final_config.json"
torch.save(model.state_dict(), model_file)
model.config.to_json_file(config_file)

[LOG] epoch 0/1


[LOG] step 0/3000
[LOG] batch {'article': tensor([[ 3791,  1971,   532,  ..., 50257, 50257, 50257]]), 'sum_idx': tensor([258])} took 0.759838342666626
[LOG] step 1/3000
loss: 40.408355712890625

After 1st update: 



/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:247: UserWarning: To get the last learning rate computed by the scheduler, please use `get_last_lr()`.
  warnings.warn("To get the last learning rate computed by the scheduler, "


new_article

CHICAGO, Illinois -LRB- Reuters -RRB- -- Grammy Award-winning R&B singer R. Kelly will go on trial September 17 on child pornography charges, five years after the accusations were first made, prosecutors said Wednesday. Jury selection in R. Kelly's trial is scheduled to begin September 17. Kelly, 40, whose real name is Robert Kelly, faces up to 15 years in jail if convicted of videotaping himself having sex with an underage girl. Prosecutors have said the girl could have been as young as 13, but defense attorneys have disputed her age and whether Kelly is on the tape. The underground videotape was widely circulated. Kelly pleaded not guilty to the charges and in the interim has released hit songs, gone on tours, and released a DVD set of `` hip-hopera '' skits. Cook County Judge Vincent Gaughan said jury selection would begin September 17. The trial was delayed, in part, by arguments over when the video was made. It was also pushed back because the judge fell and broke bon

new_article

-LRB- CNN -RRB- -- The U.S. State Department is offering $ 5 million for information leading to the `` arrest, transfer or conviction '' of three top leaders of the Lord's Resistance Army, the department announced Wednesday. One of those leaders, Joseph Kony, was the focus of a massive social media campaign called `` Kony 2012. '' Kony is wanted by the International Criminal Court at the Hague for war crimes and crimes against humanity, stemming in part from allegations that he conscripted children as soldiers and sex slaves in his army, which operates in parts of Uganda and other parts of central Africa. A small number of U.S. special forces are advising and assisting regional military efforts authorized by the African Union, the State Department said. Some of those U.S. advisers have been operating in southeastern Central African Republic, according to the department. The reward money is available through the Department of State Rewards Program Update and Technical Corre

...

CHICAGO, Illinois -LRB- Reuters -RRB- -- Grammy Award-winning R&B singer R. Kelly will go on trial September 17 on child pornography charges, five years after the accusations were first made, prosecutors said Wednesday. Jury selection in R. Kelly's trial is scheduled to begin September 17. Kelly, 40, whose real name is Robert Kelly, faces up to 15 years in jail if convicted of videotaping himself having sex with an underage girl. Prosecutors have said the girl could have been as young as 13, but defense attorneys have disputed her age and whether Kelly is on the tape. The underground videotape was widely circulated. Kelly pleaded not guilty to the charges and in the interim has released hit songs, gone on tours, and released a DVD set of `` hip-hopera '' skits. Cook County Judge Vincent Gaughan said jury selection would begin September 17. The trial was delayed, in part, by arguments over when the video was made. It was also pushed back because the judge fell and broke bones and needed

-LRB- CNN -RRB- -- The U.S. State Department is offering $ 5 million for information leading to the `` arrest, transfer or conviction '' of three top leaders of the Lord's Resistance Army, the department announced Wednesday. One of those leaders, Joseph Kony, was the focus of a massive social media campaign called `` Kony 2012. '' Kony is wanted by the International Criminal Court at the Hague for war crimes and crimes against humanity, stemming in part from allegations that he conscripted children as soldiers and sex slaves in his army, which operates in parts of Uganda and other parts of central Africa. A small number of U.S. special forces are advising and assisting regional military efforts authorized by the African Union, the State Department said. Some of those U.S. advisers have been operating in southeastern Central African Republic, according to the department. The reward money is available through the Department of State Rewards Program Update and Technical Corrections Act, w

perplexity: 6.57549524307251
After 1281 updates: 



CHICAGO, Illinois -LRB- Reuters -RRB- -- Grammy Award-winning R&B singer R. Kelly will go on trial September 17 on child pornography charges, five years after the accusations were first made, prosecutors said Wednesday. Jury selection in R. Kelly's trial is scheduled to begin September 17. Kelly, 40, whose real name is Robert Kelly, faces up to 15 years in jail if convicted of videotaping himself having sex with an underage girl. Prosecutors have said the girl could have been as young as 13, but defense attorneys have disputed her age and whether Kelly is on the tape. The underground videotape was widely circulated. Kelly pleaded not guilty to the charges and in the interim has released hit songs, gone on tours, and released a DVD set of `` hip-hopera '' skits. Cook County Judge Vincent Gaughan said jury selection would begin September 17. The trial was delayed, in part, by arguments over when the video was made. It was also pushed back because the judge fell and broke bones and needed

-LRB- CNN -RRB- -- The U.S. State Department is offering $ 5 million for information leading to the `` arrest, transfer or conviction '' of three top leaders of the Lord's Resistance Army, the department announced Wednesday. One of those leaders, Joseph Kony, was the focus of a massive social media campaign called `` Kony 2012. '' Kony is wanted by the International Criminal Court at the Hague for war crimes and crimes against humanity, stemming in part from allegations that he conscripted children as soldiers and sex slaves in his army, which operates in parts of Uganda and other parts of central Africa. A small number of U.S. special forces are advising and assisting regional military efforts authorized by the African Union, the State Department said. Some of those U.S. advisers have been operating in southeastern Central African Republic, according to the department. The reward money is available through the Department of State Rewards Program Update and Technical Corrections Act, w